---

# S05E02 : Deeper into classes & OOP - Le bestiaire des méthodes

Cyril Desjouy

--- 

L'objectif de ce notebook est de présenter les trois types de méthodes de base disponibles pour la construction de classe. Ce notebook tente d'illustrer :

* les méthodes d'instance,
* les méthodes statiques,
* les méthodes de classe.
---

## 1. ***Instance methods***

Les **méthodes d'instance** sont les méthodes de base les plus utilisées sous Python. Ce type de méthode prend toujours en premier argument `self` qui représente la future instance de la classe. Il est bien sûr possible de passer d'autres arguments à ce type de méthode. Les méthodes d'instance peuvent accéder par l'intermédiaire de `self` à tous les autres attributs et méthodes de la classe. Elles peuvent également accéder à la classe elle-même par l'intermédiaire de `self.__class__`.

Prenons l'exemple suivant:

In [24]:
class Tree:
    
    def __init__(self, name):
        self.name = name
        
    def talk(self):
        if self.name.lower() == 'groot':
            return 'I am Groot'
        return '...'

* **Depuis la classe**, la méthode `talk` est considérée comme une fonction classique et la classe l'entourant est son ***namespace***. Cette méthode prend `self` en premier argument, mais n'est attachée à aucune instance de `Tree`. On ne peut donc pas l'appeler directement : 
```python
>> Tree.talk
<function __main__.Tree.talk(self)>           # Seems like a classical function!
>> Tree.talk()                                # raises TypeError
```

* **Depuis une instance**, la méthode `talk` est considérée comme une ***bound method***. Elle est alors *attachée* à une instance:
```python
>> groot = Character("groot")
>> groot.talk                                 # Method bound to Tree object
<bound method Tree.talk of <__main__.Tree object at 0x7fe5a8607550>>
>> groot.talk()
'I am Groot'
```

En fait, lorsque la méthode `talk` est appelée, l'interpréteur Python remplace l'argument `self` par l'instance de la classe. Écrire `groot.talk()` est finalement un raccourci vers `Tree.talk(groot)`. Les méthodes d'instance sont extrêmement puissantes car elles peuvent modifier directement l'état de l'instance mais également l'état de la classe elle-même.

---

## 2. ***Class methods***

Les **méthodes de classe** sont des méthodes qui ne sont pas rattachées à une instance, mais à une classe. Elle prennent en premier argument la classe elle-même appelée par convention `cls`. Il est bien sûr possible de passer d'autres arguments à ce type de méthode. Les méthodes de classe ne peuvent pas modifier l'état de l'instance (elle n'ont pas accès à `self`) mais peuvent modifier l'état de la classe. Notez que la modification de l'état d'une classe s'applique à toutes les instances de cette classe comme nous l'avons vu lorsque nous avons abordé les attributs de classe dans le notebook précédent.

Pour déclarer une ***class method***, il est nécessaire d'utiliser le décorateur `@classmethod`. Par exemple:

In [2]:
class Tree:
    
    trunk_color = 'brown'    
    
    @classmethod
    def color(cls):
        return cls.trunk_color

Dans l'exemple précédent, la méthode `color` a accès aux attribut de classe grâce à `cls`. L'appel des méthodes de classe est similaire à l'appel des méthode d'instance:
```python
>> Tree.color                                 # Method bound to class Tree
<bound method Tree.color of <class '__main__.Tree'>>
>> Tree.color()
'brown'
```
Notez que l'interpréteur Python passe automatiquement la classe en premier argument lorsque `Tree.color()` est appelée.

Parmi les utilisations courantes des méthodes de classes, citons en particulier les ***factory methods*** qui permettent de construire des objets personnalisés. Par exemple :

In [32]:
class Tree:
    
    def __init__(self, name):
        self.name = name
    
    def talk(self):
        if self.name.lower() == 'groot':
            return 'I am Groot'
        elif self.name.lower() == 'fangorn':
            return 'I am not going to tell you my name, not yet at any rate.'
        return '...'
       
    @classmethod
    def groot(cls):
        return cls('Groot')
    
    @classmethod
    def fangorn(cls):
        return cls('Fangorn')

L'appel des méthodes de classe `groot` et `fangorn` permettent alors de créer des instances particulières de la classe `Tree`:
```python
>> Tree.fangorn()          # Returns the object <__main__.Tree at 0x7f2c704b2090>
>> Tree.groot()            # Returns the object <__main__.Tree at 0x7f2c704ca9d0>
>> Tree.groot().talk()     # Returns 'I am Groot'
```

Même si Python limite les classes a une seule méthode `__init__`, les méthodes de classe offre entre autres la possibilité d'ajouter autant de constructeurs alternatifs que nécessaire. 

---

## 3. ***Static methods***

Les **méthodes statiques** sont généralement utilisées lorsqu'il s'agit d'écrire une méthode qui appartient à une classe mais qui n'utilise ni l'objet `self`, ni l'objet `cls`. Les méthodes statiques ne peuvent accéder ni à l'état de l'instance, ni à l'état de la classe. Elle peuvent prendre un nombre arbitraire d'argument comme toute autre fonction ou méthode. 

Pour déclarer une ***static method***, il est nécessaire d'utiliser le décorateur `@staticmethod`. Par exemple:

In [13]:
class Tree:
    
    def __init__(self, name):
        self.name = name
        
    def talk(self):
        if self.name.lower() == 'groot':
            return 'I am {}'.format(self.name.capitalize())
        return '...'
    
    @staticmethod
    def this(pretty_thing=''):
        return f'{pretty_thing} This is a Tree {pretty_thing}'

En fait, le décorateur `@staticmethod` force l'interpréteur Python à ne pas passer l'instance à cette méthode (`self`). Les ***static methods*** fonctionnent comme des fonctions ordinaires sauf qu'elles appartiennent au ***namespace*** d'une classe.
```python
>> groot = Tree("groot")
>> groot.this                         # Function not bound to class nor instance
<function __main__.Tree.this(name)>
>> groot.this('**')
'** This is a Tree **'
```

Notons qu'une ***bound method*** est instanciée pour chaque instance d'une classe alors que ce n'est pas le cas pour les ***static methods***:
```python
>> Tree('').talk == Tree('').talk
False
>> Tree('').this == Tree('').this
True
```

---

## 4. Communication entre les différents types de méthodes

Considérons l'exemple suivant:

In [38]:
class Tree:
    
    trunk_color = 'brown'    
    
    def color_from_instance(self):
        return self.pretty(self.trunk_color) 
    
    @classmethod
    def color_from_class(cls):
        return cls.pretty(cls.trunk_color)
    
    @staticmethod
    def pretty(attribute):
        return '** {} **'.format(attribute)

Comme nous l'avons vu précédemment, les méthodes statiques sont accessibles depuis la classe ou l'instance. Il est donc possible d'appeler une méthode statique depuis une méthode d'instance ou une méthode de classe:
```python
>> Tree().color_from_instance()      # Returns ** brown **
>> Tree().color_from_class()         # Returns ** brown **
```


---

## 5. Résumé

In [39]:
class Example:
    
    def method1():                     # No "self" argument
        return 'class only'

    def method2(self):                 # "self" argument
        return 'instance only'
    
    @classmethod
    def method3(cls):                  # cls argument and classmethod decorator
        return 'class or instance'
    
    @staticmethod
    def method4():                     # No "self" argument nor 'cls' but staticmethod decorator
        return 'class or instance'

### 5.1. Méthodes appelées sur la classe

```python
>> Example.method1()    # returns 'class only'
>> Example.method2()    # raises TypeError
>> Example.method3()    # returns 'class or instance'
>> Example.method4()    # returns 'class or instance'
```

### 5.2. Méthodes appelées sur l'instance

```python
>> Example().method1()   # raises TypeError
>> Example().method2()   # returns 'instance only'
>> Example().method3()   # returns 'class or instance'
>> Example().method3()   # returns 'class or instance'
```

---

## Application

<div class="alert alert-block alert-info">
Reprenez la classe <code>Troll</code> du précédent notebook:
</div>

```python
class Troll:
    
    appearance = 'ugly'     
     
    def __init__(self, name):
        self.name = name          
```

<div class="alert alert-block alert-info">
Vous ajouterez à cette classe une méthode <code>magic_spell</code> permettant de rendre tous les <code>Troll</code> séduisants. 
</div>